In [1]:
import pandas as pd
import pandas_profiling as pp


In [2]:
import os
data_path = '/home/srgrace/genericContest_data/cat-in-the-dat-ii'

train = pd.read_csv(os.path.join(data_path, 'train.csv'))
test = pd.read_csv(os.path.join(data_path, 'test.csv'))

In [3]:
train.head()

id  bin_0  bin_1  bin_2 bin_3 bin_4 nom_0      nom_1    nom_2       nom_3  \
0   0    0.0    0.0    0.0     F     N   Red  Trapezoid  Hamster      Russia   
1   1    1.0    1.0    0.0     F     Y   Red       Star  Axolotl         NaN   
2   2    0.0    1.0    0.0     F     N   Red        NaN  Hamster      Canada   
3   3    NaN    0.0    0.0     F     N   Red     Circle  Hamster     Finland   
4   4    0.0    NaN    0.0     T     N   Red   Triangle  Hamster  Costa Rica   

   ...        nom_9 ord_0        ord_1     ord_2 ord_3 ord_4  ord_5  day  \
0  ...    02e7c8990   3.0  Contributor       Hot     c     U     Pw  6.0   
1  ...    f37df64af   3.0  Grandmaster      Warm     e     X     pE  7.0   
2  ...          NaN   3.0          NaN  Freezing     n     P     eN  5.0   
3  ...    f9d456e57   1.0       Novice  Lava Hot     a     C    NaN  3.0   
4  ...    c5361037c   3.0  Grandmaster      Cold     h     C     OZ  5.0   

  month target  
0   3.0      0  
1   7.0      0  
2   9.0      0  
3   3.0      0  
4  12.0      0  

[5 rows x 25 columns]

In [4]:
test.head()

id  bin_0  bin_1  bin_2 bin_3 bin_4 nom_0    nom_1    nom_2  \
0  600000    0.0    0.0    0.0     F     Y  Blue  Polygon  Axolotl   
1  600001    0.0    0.0    0.0     F     Y   Red   Circle     Lion   
2  600002    0.0    0.0    0.0     F     Y  Blue   Circle  Axolotl   
3  600003    1.0    0.0    0.0     F     N   Red  Polygon  Axolotl   
4  600004    0.0    0.0    1.0     F     Y   Red   Circle      NaN   

        nom_3  ...       nom_8      nom_9 ord_0        ord_1        ord_2  \
0     Finland  ...   ca9ad1d4b  fced9e114   3.0       Novice  Boiling Hot   
1      Russia  ...   060a21580  7ca8775da   1.0       Novice         Cold   
2      Russia  ...   165e81a00  5940334c9   1.0       Expert         Warm   
3  Costa Rica  ...   77d41330d  6fbdeefc8   1.0       Expert          Hot   
4     Finland  ...   2218d9dfe  2a27c8fde   1.0  Contributor     Lava Hot   

  ord_3  ord_4 ord_5  day month  
0     f      U    oU  3.0   9.0  
1     n      N   NaN  2.0   8.0  
2     i      N    DN  2.0   6.0  
3     m      B    AG  1.0   6.0  
4     o      J    DT  3.0   3.0  

[5 rows x 24 columns]

In [5]:
import warnings
warnings.filterwarnings("ignore")

import gc
import joblib
import numpy as np
import tensorflow as tf
from sklearn.model_selection import StratifiedKFold
from sklearn import metrics, preprocessing
from tensorflow.keras import layers
from tensorflow.keras import optimizers
from tensorflow.keras.models import Model, load_model
from tensorflow.keras import callbacks
from tensorflow.keras import backend as K
from tensorflow.keras import utils

In [6]:
test['target'] = -1
data = pd.concat([train, test]).reset_index(drop=True)

features = [x for x in train.columns if x not in ['id', 'target']]

for feat in features:
    label_enc = preprocessing.LabelEncoder()
    data[feat] = label_enc.fit_transform(data[feat].fillna('-1').astype(str).values)

In [7]:
train = data[data.target != -1].reset_index(drop=True)
test = data[data.target == -1].reset_index(drop=True)

In [8]:
train.sample(5)

id  bin_0  bin_1  bin_2  bin_3  bin_4  nom_0  nom_1  nom_2  nom_3  \
45976    45976      1      1      1      1      2      3      6      3      6   
185790  185790      1      1      2      1      1      3      2      5      3   
81693    81693      1      1      1      1      2      1      2      5      3   
89677    89677      1      1      2      0      1      3      4      6      6   
183136  183136      1      1      1      2      1      1      5      5      6   

         ...    nom_9  ord_0  ord_1  ord_2  ord_3  ord_4  ord_5  day  month  \
45976    ...     1782      2      2      5     14      5     98    3      9   
185790   ...     1995      1      4      2      8     25    181    6      5   
81693    ...      856      2      5      3      8     15      3    5      9   
89677    ...     1332      2      1      3      3     20    150    3      5   
183136   ...      599      3      3      5      4      5     34    5      6   

        target  
45976        0  
185790       0  
81693        0  
89677        0  
183136       0  

[5 rows x 25 columns]

In [9]:
pp.ProfileReport(train)

In [9]:
def auc(y_true, y_pred):
    def fallback_auc(y_true, y_pred):
        try:
            return metrics.roc_auc_score(y_true, y_pred)
        except:
            return 0.5
    return tf.py_function(fallback_auc, (y_true, y_pred), tf.double)

In [10]:
def create_model(data, feats):
    inps = []
    outs = []
    for feat in feats:
        num_unique_vals = int(data[feat].nunique())
        embed_dim = int(min(np.ceil(num_unique_vals/2), 50))
        
        inp = layers.Input(shape=(1, ))
        out = layers.Embedding(num_unique_vals + 1, embed_dim, name=feat)(inp)
        
        out = layers.SpatialDropout1D(0.3)(out)
        out = layers.Reshape(target_shape=(embed_dim, ))(out)
        
        inps.append(inp)
        outs.append(out)
    
    x = layers.Concatenate()(outs)
    x = layers.BatchNormalization()(x)
    
    x = layers.Dense(300, activation='relu')(x)
    x = layers.Dropout(0.3)(x)
    x = layers.BatchNormalization()(x)
    
    x = layers.Dense(300, activation='relu')(x)
    x = layers.Dropout(0.3)(x)
    x = layers.BatchNormalization()(x)
    
    x = layers.Dense(300, activation='relu')(x)
    x = layers.Dropout(0.3)(x)
    x = layers.BatchNormalization()(x)
    
    y = layers.Dense(2, activation='softmax')(x)
    
    model = Model(inputs=inps, outputs=y)
    return model

In [11]:
test_data = [test.loc[:, features].values[:, k] for k in range(test.loc[:, features].values.shape[1])]
oof_preds = np.zeros((len(train)))
test_preds = np.zeros((len(test)))


skf = StratifiedKFold(n_splits=50)
for train_idx, test_idx in skf.split(train, train.target.values):
    
    x_train, x_test = train.iloc[train_idx, :], train.iloc[test_idx, :]
    x_train = x_train.reset_index(drop=True)
    x_test = x_test.reset_index(drop=True)
    
    y_train, y_test = x_train.target.values, x_test.target.values
    
    model = create_model(data, features)
    model.compile(loss='binary_crossentropy', optimizers='adam', metrics=[auc])
    
    x_train = [x_train.loc[:, features].values[:, k] for k in range(x_train.loc[:, features].values.shape[1])]
    x_test = [x_test.loc[:, features].values[:, k] for k in range(x_test.loc[:, features].values.shape[1])]
    
    early_stop = callbacks.EarlyStopping(monitor='val_auc', min_delta=0.001, patience=5, verbose=1, mode='max',
                                         baseline=None, restore_best_weights=True)
    
    reduce_lr = callbacks.ReduceLROnPlateau(monitor='val_auc', factor=0.5, patience=3, min_lr=1e-6, 
                                           mode='max', verbose=1)
    
    model.fit(x_train, utils.to_categorical(y_train),
             validation_data=(x_test, utils.to_categorical(y_test)),
             verbose=1, batch_size=1024, callbacks=[early_stop, reduce_lr], epochs=100)
    
    valid_fold_preds = model.predict(x_test)[:, 1]
    test_fold_preds = model.predict(test_data)[:, 1]
    oof_preds[test_idx] = valid_fold_preds.ravel()
    test_preds += test_fold_preds.ravel()
    print(metrics.roc_auc_score(y_test, valid_fold_preds))
    K.clear_session()

Train on 587999 samples, validate on 12001 samples
Epoch 1/100


587999/587999 [==============================] - 31s 53us/sample - loss: 0.4555 - auc: 0.7110 - val_loss: 0.4043 - val_auc: 0.7769
Epoch 2/100
587999/587999 [==============================] - 23s 39us/sample - loss: 0.4073 - auc: 0.7729 - val_loss: 0.4073 - val_auc: 0.7784
Epoch 3/100
587999/587999 [==============================] - 22s 38us/sample - loss: 0.4034 - auc: 0.7789 - val_loss: 0.4031 - val_auc: 0.7807
Epoch 4/100
587999/587999 [==============================] - 22s 38us/sample - loss: 0.4014 - auc: 0.7816 - val_loss: 0.4061 - val_auc: 0.7820
Epoch 5/100
587999/587999 [==============================] - 34s 57us/sample - loss: 0.3996 - auc: 0.7840 - val_loss: 0.4012 - val_auc: 0.7805
Epoch 6/100
587999/587999 [==============================] - 27s 46us/sample - loss: 0.3984 - auc: 0.7858 - val_loss: 0.4044 - val_auc: 0.7810
Epoch 7/100
587776/587999 [============================>.] - ETA: 0s - loss: 0.3975 - auc: 0.7871
Epoch 00007: ReduceLROnPlateau reducing learning rate to

Epoch 3/100
587999/587999 [==============================] - 24s 41us/sample - loss: 0.4032 - auc: 0.7789 - val_loss: 0.4000 - val_auc: 0.7853
Epoch 4/100
587999/587999 [==============================] - 23s 39us/sample - loss: 0.4014 - auc: 0.7817 - val_loss: 0.4009 - val_auc: 0.7858
Epoch 5/100
587999/587999 [==============================] - 24s 41us/sample - loss: 0.3998 - auc: 0.7840 - val_loss: 0.3995 - val_auc: 0.7846
Epoch 6/100
587999/587999 [==============================] - 25s 42us/sample - loss: 0.3988 - auc: 0.7856 - val_loss: 0.3984 - val_auc: 0.7845
Epoch 7/100
586752/587999 [============================>.] - ETA: 0s - loss: 0.3975 - auc: 0.7869
Epoch 00007: ReduceLROnPlateau reducing learning rate to 0.0005000000237487257.
587999/587999 [==============================] - 23s 39us/sample - loss: 0.3975 - auc: 0.7869 - val_loss: 0.4002 - val_auc: 0.7827
Epoch 8/100
587999/587999 [==============================] - 21s 36us/sample - loss: 0.3944 - auc: 0.7910 - val_loss: 0

Epoch 6/100
587999/587999 [==============================] - 23s 39us/sample - loss: 0.3963 - auc: 0.7883 - val_loss: 0.3991 - val_auc: 0.7858
Epoch 00006: early stopping
0.7848010547679412
Train on 587999 samples, validate on 12001 samples
Epoch 1/100
587999/587999 [==============================] - 29s 50us/sample - loss: 0.4573 - auc: 0.7066 - val_loss: 0.4059 - val_auc: 0.7641
Epoch 2/100
587999/587999 [==============================] - 26s 44us/sample - loss: 0.4072 - auc: 0.7732 - val_loss: 0.4010 - val_auc: 0.7605
Epoch 3/100
587999/587999 [==============================] - 32s 54us/sample - loss: 0.4035 - auc: 0.7788 - val_loss: 0.4021 - val_auc: 0.7662
Epoch 4/100
587999/587999 [==============================] - 26s 44us/sample - loss: 0.4019 - auc: 0.7811 - val_loss: 0.4018 - val_auc: 0.7684
Epoch 5/100
587999/587999 [==============================] - 35s 59us/sample - loss: 0.3999 - auc: 0.7836 - val_loss: 0.4054 - val_auc: 0.7627
Epoch 6/100
587999/587999 [=================

587999/587999 [==============================] - 24s 42us/sample - loss: 0.3997 - auc: 0.7842 - val_loss: 0.3980 - val_auc: 0.7636
Epoch 6/100
587776/587999 [============================>.] - ETA: 0s - loss: 0.3984 - auc: 0.7859
Epoch 00006: ReduceLROnPlateau reducing learning rate to 0.0005000000237487257.
587999/587999 [==============================] - 27s 46us/sample - loss: 0.3984 - auc: 0.7860 - val_loss: 0.3996 - val_auc: 0.7625
Epoch 7/100
587999/587999 [==============================] - 28s 48us/sample - loss: 0.3945 - auc: 0.7910 - val_loss: 0.4015 - val_auc: 0.7611
Epoch 8/100
587999/587999 [==============================] - 26s 44us/sample - loss: 0.3939 - auc: 0.7916 - val_loss: 0.4020 - val_auc: 0.7596
Epoch 00008: early stopping
0.7860930515058512
Train on 587999 samples, validate on 12001 samples
Epoch 1/100
587999/587999 [==============================] - 30s 51us/sample - loss: 0.4576 - auc: 0.7097 - val_loss: 0.4010 - val_auc: 0.7610
Epoch 2/100
587999/587999 [======

0.7881146337873413
Train on 587999 samples, validate on 12001 samples
Epoch 1/100
587999/587999 [==============================] - 29s 48us/sample - loss: 0.4580 - auc: 0.7067 - val_loss: 0.4133 - val_auc: 0.7391
Epoch 2/100
587999/587999 [==============================] - 23s 38us/sample - loss: 0.4071 - auc: 0.7735 - val_loss: 0.3993 - val_auc: 0.7411
Epoch 3/100
587999/587999 [==============================] - 23s 38us/sample - loss: 0.4032 - auc: 0.7790 - val_loss: 0.4015 - val_auc: 0.7413
Epoch 4/100
587999/587999 [==============================] - 23s 40us/sample - loss: 0.4015 - auc: 0.7816 - val_loss: 0.3987 - val_auc: 0.7409
Epoch 5/100
587999/587999 [==============================] - 23s 38us/sample - loss: 0.4000 - auc: 0.7835 - val_loss: 0.4034 - val_auc: 0.7411
Epoch 6/100
587776/587999 [============================>.] - ETA: 0s - loss: 0.3983 - auc: 0.7861
Epoch 00006: ReduceLROnPlateau reducing learning rate to 0.0005000000237487257.
587999/587999 [======================

Epoch 3/100
588001/588001 [==============================] - 28s 48us/sample - loss: 0.4032 - auc: 0.7791 - val_loss: 0.4125 - val_auc: 0.7383
Epoch 4/100
588001/588001 [==============================] - 27s 46us/sample - loss: 0.4012 - auc: 0.7822 - val_loss: 0.4091 - val_auc: 0.7525
Epoch 5/100
588001/588001 [==============================] - 22s 38us/sample - loss: 0.3995 - auc: 0.7844 - val_loss: 0.4039 - val_auc: 0.7549
Epoch 6/100
588001/588001 [==============================] - 25s 43us/sample - loss: 0.3986 - auc: 0.7856 - val_loss: 0.4025 - val_auc: 0.7536
Epoch 7/100
588001/588001 [==============================] - 27s 45us/sample - loss: 0.3971 - auc: 0.7877 - val_loss: 0.4055 - val_auc: 0.7521
Epoch 8/100
587776/588001 [============================>.] - ETA: 0s - loss: 0.3961 - auc: 0.7891
Epoch 00008: ReduceLROnPlateau reducing learning rate to 0.0005000000237487257.
588001/588001 [==============================] - 27s 45us/sample - loss: 0.3961 - auc: 0.7891 - val_loss: 0

Epoch 7/100
588001/588001 [==============================] - 23s 39us/sample - loss: 0.3955 - auc: 0.7895 - val_loss: 0.4002 - val_auc: 0.7594
Epoch 8/100
588001/588001 [==============================] - 23s 39us/sample - loss: 0.3943 - auc: 0.7913 - val_loss: 0.4015 - val_auc: 0.7589
Epoch 00008: early stopping
0.7851076988983183
Train on 588001 samples, validate on 11999 samples
Epoch 1/100
588001/588001 [==============================] - 29s 49us/sample - loss: 0.4567 - auc: 0.7099 - val_loss: 0.3982 - val_auc: 0.7903
Epoch 2/100
588001/588001 [==============================] - 24s 41us/sample - loss: 0.4070 - auc: 0.7733 - val_loss: 0.4005 - val_auc: 0.7927
Epoch 3/100
588001/588001 [==============================] - 23s 40us/sample - loss: 0.4032 - auc: 0.7795 - val_loss: 0.3999 - val_auc: 0.7894
Epoch 4/100
588001/588001 [==============================] - 24s 41us/sample - loss: 0.4013 - auc: 0.7817 - val_loss: 0.3959 - val_auc: 0.7911
Epoch 5/100
586752/588001 [=================

588001/588001 [==============================] - 23s 40us/sample - loss: 0.3945 - auc: 0.7908 - val_loss: 0.4049 - val_auc: 0.7783
Epoch 00008: early stopping
0.781378590819237
Train on 588001 samples, validate on 11999 samples
Epoch 1/100
588001/588001 [==============================] - 26s 45us/sample - loss: 0.4555 - auc: 0.7122 - val_loss: 0.4022 - val_auc: 0.7926
Epoch 2/100
588001/588001 [==============================] - 21s 36us/sample - loss: 0.4070 - auc: 0.7736 - val_loss: 0.4089 - val_auc: 0.7930
Epoch 3/100
588001/588001 [==============================] - 22s 37us/sample - loss: 0.4036 - auc: 0.7786 - val_loss: 0.4051 - val_auc: 0.7932
Epoch 4/100
588001/588001 [==============================] - 21s 36us/sample - loss: 0.4012 - auc: 0.7820 - val_loss: 0.4023 - val_auc: 0.7916
Epoch 5/100
588001/588001 [==============================] - 24s 41us/sample - loss: 0.3996 - auc: 0.7841 - val_loss: 0.4004 - val_auc: 0.7928
Epoch 6/100
587776/588001 [============================>.

Epoch 00008: early stopping
0.7931852874641216
Train on 588001 samples, validate on 11999 samples
Epoch 1/100
588001/588001 [==============================] - 28s 47us/sample - loss: 0.4582 - auc: 0.7081 - val_loss: 0.4027 - val_auc: 0.7875
Epoch 2/100
588001/588001 [==============================] - 22s 37us/sample - loss: 0.4075 - auc: 0.7729 - val_loss: 0.4012 - val_auc: 0.7896
Epoch 3/100
588001/588001 [==============================] - 22s 37us/sample - loss: 0.4030 - auc: 0.7796 - val_loss: 0.3964 - val_auc: 0.7899
Epoch 4/100
588001/588001 [==============================] - 22s 37us/sample - loss: 0.4009 - auc: 0.7825 - val_loss: 0.3973 - val_auc: 0.7885
Epoch 5/100
588001/588001 [==============================] - 22s 38us/sample - loss: 0.3999 - auc: 0.7836 - val_loss: 0.3968 - val_auc: 0.7897
Epoch 6/100
587776/588001 [============================>.] - ETA: 0s - loss: 0.3984 - auc: 0.7859
Epoch 00006: ReduceLROnPlateau reducing learning rate to 0.0005000000237487257.
588001/58

In [12]:
print("Overall AUC={}".format(metrics.roc_auc_score(train.target.values, oof_preds)))

Overall AUC=0.782480002734998


In [13]:
test_preds /= 50
test_ids = test.id.values
print("Saving submission file")
submission = pd.DataFrame.from_dict({
    'id': test_ids,
    'target': test_preds
})
submission.to_csv("data/submission-23.csv", index=False)

Saving submission file
